In [9]:
from huggingface_hub import list_datasets
from toolz import concat
from toolz import groupby
from toolz import valmap
from toolz import frequencies

## Grab datasets with `token-classification` task

In [3]:
datasets = list(list_datasets(filter="task_categories:token-classification"))

In [4]:
datasets[0]

DatasetInfo(id='acronym_identification', author=None, sha='c3c245a18bbd57b1682b099e14460eebf154cbdf', last_modified=datetime.datetime(2023, 1, 25, 14, 18, 28, tzinfo=datetime.timezone.utc), private=False, gated=False, disabled=False, downloads=1823, likes=17, paperswithcode_id='acronym-identification', tags=['task_categories:token-classification', 'annotations_creators:expert-generated', 'language_creators:found', 'multilinguality:monolingual', 'size_categories:10K<n<100K', 'source_datasets:original', 'language:en', 'license:mit', 'acronym-identification', 'arxiv:2010.14678', 'region:us'], card_data=None, siblings=None)

In [19]:
with_language= [dataset for dataset in datasets if "language" in [t.split(":")[0] for t in dataset.tags]]

In [20]:
with_language[0]

DatasetInfo(id='acronym_identification', author=None, sha='c3c245a18bbd57b1682b099e14460eebf154cbdf', last_modified=datetime.datetime(2023, 1, 25, 14, 18, 28, tzinfo=datetime.timezone.utc), private=False, gated=False, disabled=False, downloads=1823, likes=17, paperswithcode_id='acronym-identification', tags=['task_categories:token-classification', 'annotations_creators:expert-generated', 'language_creators:found', 'multilinguality:monolingual', 'size_categories:10K<n<100K', 'source_datasets:original', 'language:en', 'license:mit', 'acronym-identification', 'arxiv:2010.14678', 'region:us'], card_data=None, siblings=None)

In [23]:
def get_languages(dataset):
    tags = list(dataset.tags)
    languages = [t for t in tags if t.split(':')[0]=='language']
    languages = [language for language in languages if len(language.split(":"))==2]
    return [t.split(":")[1] for t in languages] 

In [24]:
freqs = frequencies(concat(get_languages(dataset) for dataset in with_language))
freqs = dict(sorted(freqs.items(), key=lambda x: x[1],reverse=True))

In [28]:
from huggingface_hub import list_models

In [36]:
from huggingface_hub import ModelFilter
from tqdm.auto import tqdm

In [38]:
no_model = []
for lang in tqdm(freqs.keys()):
    models_for_lang_with_task_token_classification = list(
        list_models(filter=ModelFilter(language=lang, task="token-classification"))
    )
    models_for_lang_any_task = list(list_models(filter=ModelFilter(language=lang)))
    if not models_for_lang_with_task_token_classification:
        data = {
            "language": lang,
            "datasets": freqs[lang],
            "token_classification_models": len(
                models_for_lang_with_task_token_classification
            ),
            "all_models": len(models_for_lang_any_task),
        }
        no_model.append(data)

  0%|          | 0/393 [00:00<?, ?it/s]

In [ ]:
len(no_model)

246